# Introduction

This is the audience overlap and analysis example notebook. It runs the Snowflake-provided Audience Overlap & Segmentation template in code.
With this template, the provider and consumer link tables into the clean room, the provider specifies which columns to join on,
which columns to show, group by, and perform aggregation functions on.

Join columns, which are typically entity identifiers such as emails, cannot appear in the results.

The template applies differential privacy to protect individual entities; this requires any column that appears in the results to either
have an aggregation policy applied or to be part of a GROUP BY statement.

This template is available in the web application, with built-in features including options for activation and provider-run analysis.

You must have two separate clean-room-enabled Snowflake accounts to run this notebook. Use one account for the provider and the other
for the consumer. Both accounts must be in the same Snowflake organization and same web hosting region. Open and install this notebook
in each account, and run the appropriate code for each account, starting with the provider account.

You can find more information at https://docs.snowflake.com/en/user-guide/cleanrooms/demo-flows/basic-flow-overlap

# Provider

Use your provider account to create a clean room with the name 'Overlap Analysis Demo Clean Room'. If a clean room exists in this account
with that name, the process will fail, and you should choose a new name here and in the consumer section.

## Set up the environment and create the clean room

The INTERNAL argument to `cleanroom_init` indicates that this clean room is available only within the same organization.
To share a clean room with an account in a different organization, specify EXTERNAL, which triggers a security scan that takes up to 24
hours to complete.

In [ ]:

-- Set up your environment
USE ROLE samooha_app_role;
USE WAREHOUSE app_wh;

-- Create the clean room. If a clean room with this name already exists, this process will fail, and you should choose a 
-- different clean room name.
SET cleanroom_name = 'Overlap Analysis Demo Clean Room';
CALL samooha_by_snowflake_local_db.provider.cleanroom_init($cleanroom_name, 'INTERNAL');

-- Set the release directive, which is the version shared to collaborators.
CALL samooha_by_snowflake_local_db.provider.set_default_release_directive($cleanroom_name, 'V1_0', '0');



## Link your data into the clean room

This code uses the sample database that is available with all clean room environments.

In [ ]:
CALL samooha_by_snowflake_local_db.provider.link_datasets($cleanroom_name, ['SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS']);

-- Look at the dataset you just installed.
CALL samooha_by_snowflake_local_db.provider.view_provider_datasets($cleanroom_name);

In [ ]:
-- A quick view of what's in the table you just linked.
SELECT * FROM SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS LIMIT 10;

## Set the provider join policy

Specify which columns from your data the consumer is allowed to join on when running templates within the clean room. Join columns in an
overlap analysis are typically entity-identifying information, such as email or Social Security number. Join columns cannot be projected.

If you were to omit setting a join policy, all provider columns would be joinable (without any restriction on whether they can be projected).

In [ ]:
CALL samooha_by_snowflake_local_db.provider.set_join_policy($cleanroom_name, ['SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS:HASHED_EMAIL']);

-- View the join policy you just created.
CALL samooha_by_snowflake_local_db.provider.view_join_policy($cleanroom_name);

## Add the Audience Overlap & Segmentation template to the clean room

Add the Overlap & Segmentation template provided by Snowflake. This template enables a consumer to perform an overlap analysis
between datasets linked in the clean room on provider-approved columns.

Templates are written in JinjaSQL. Learn more about templates and how to create your own at
https://docs.snowflake.com/en/user-guide/cleanrooms/custom-templates

In [ ]:
CALL samooha_by_snowflake_local_db.provider.add_templates($cleanroom_name, ['prod_overlap_analysis']);

-- View the template you just added to understand how it works (if you understand JinjaSQL).
CALL samooha_by_snowflake_local_db.provider.view_added_templates($cleanroom_name);

## Set the provider column policy for the template.

Specify which columns in your dataset can be projected, aggregated, or grouped by. Join columns cannot be specified here; a column 
is either a joinable column or a projectable column, but not both (unless you omit the join policy). A column policy is associated with a
template, and each template can have different column policies. A join policy is associated with a table.

In [ ]:
CALL samooha_by_snowflake_local_db.provider.set_column_policy($cleanroom_name, [
'prod_overlap_analysis:SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS:STATUS', 
'prod_overlap_analysis:SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS:AGE_BAND', 
'prod_overlap_analysis:SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS:DAYS_ACTIVE', 
'prod_overlap_analysis:SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS:REGION_CODE']);

-- View the column policy you just specified.
CALL samooha_by_snowflake_local_db.provider.view_column_policy($cleanroom_name);

## Share the clean room

Share the clean room with your consumer account in the format <ORGANIZATION>.<ACCOUNT_NAME> for the <CONSUMER_DATA_SHARING_ACCOUNT_ID> argument.

In [ ]:
CALL samooha_by_snowflake_local_db.provider.add_consumers($cleanroom_name, '<CONSUMER_ACCOUNT_LOCATOR>', '<CONSUMER_DATA_SHARING_ACCOUNT_ID>');

-- View the consumers you invited to use your clean room.
CALL samooha_by_snowflake_local_db.provider.view_consumers($cleanroom_name);

## Publish the clean room

In [ ]:
CALL samooha_by_snowflake_local_db.provider.create_or_update_cleanroom_listing($cleanroom_name);

# Consumer

Switch to your consumer account, where you will accept the clean room invitation, link in your own data, set your own join and column
policies, and run an analysis.

Accepting an invitation installs the native application for that clean room in your account. Installing a clean room can take a minute or
more.

## Accept the invitation

Install (or *join*) the clean room.

In [ ]:
-- Set up the environment.
USE ROLE samooha_app_role;
USE WAREHOUSE app_wh;

-- Install the clean room with the name assigned by the provider account.
-- You must specify the provider's Snowflake account locator (not name).
SET cleanroom_name = 'Overlap Analysis Demo Clean Room';
CALL samooha_by_snowflake_local_db.consumer.install_cleanroom($cleanroom_name, '<PROVIDER_ACCOUNT_LOCATOR>');


## Register and link your data

The consumer account links their data into the clean room.

In [ ]:
-- Link your data into the clean room
CALL samooha_by_snowflake_local_db.consumer.link_datasets($cleanroom_name, ['SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS']);

-- Confirm that your data has been linked.
CALL samooha_by_snowflake_local_db.consumer.view_consumer_datasets($cleanroom_name);

This example does not specify join and column policies for the consumer account, because this clean room enables only consumer-run analysis:
the provider cannot see consumer data. Not providing a join policy on your data means that all columns in your data can be joined on; not
providing a column policy means that all columns in your data can be projected.

**In real world usage, consumers should specify join and policies** for their data even in clean rooms are limited to consumer-run analysis,
in case the clean room is later updated to allow provider-run analysis and you forget to add the policy later. (Note that every provider-run
analysis must first be approved by the consumer, so a provider cannot arbitrarily change the clean room policy and then analyze consumer
data without consumer oversight.)

## Run the analysis

The template joins one provider and one consumer table on one or more pairs of join columns. All projected columns must either be part of
an aggregation function or a group-by clause. The template shows the overlapping entities, grouped or aggregated as specified, between the
specified tables. The projected columns are the union of the columns listed in the `dimensions` and `measure_column` arguments. Columns
in `dimensions` are grouped; columns in `measure_column` have your designated aggregation function applied to them.

All column names must be prefixed by `p.` or `c.` (case-sensitive) depending on whether the column comes from the provider or consumer
table. If you provide more than one provider or consumer table, index the table names as `p0.`, `p1.`, `p2.`, `c0.`, `c1.`, `c2.`, and so on.
For example: `p.age` or `c.email`.

The template takes the following parameters:

- One or more consumer tables, passed in to the third argument. 
- An equal number of provider tables, passed in to the fourth argument.
- The arguments object includes the following items:
  - `dimensions`: One or more columns to show and group by in the results. All provider columns listed here must be in your provider
    column policy.
  - `measure_column`: One or more columns to show in the results, with aggregation functions specified by `measure_type` array.
    All columns listed here must be in your provider column policy.
  - `measure_type`: A parallel list of aggregation functions to apply to the columns in `measure_column`. That is, the first function
    in `measure_type` is applied to the first column in `measure_column`; the second function is applied to the second column,
    and so on.
  - `where_clause`: Pairs of join columns to use in a valid SQL WHERE clause. For example: `p.age = c.age` or
    `p.age = c.age AND p.email = c.email`. All provider columns listed here must be listed in your provider join policy."

In [ ]:
-- Run the analysis. Results of the analysis are presented in Snowsight.
CALL samooha_by_snowflake_local_db.consumer.run_analysis(
  $cleanroom_name,                    -- Cleanroom name
  'prod_overlap_analysis',            -- Template name

  ['SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS'], -- Consumer tables to use in the analysis
  
  ['SAMOOHA_SAMPLE_DATABASE.DEMO.CUSTOMERS'],  -- Provider tables to use in the analysis

  object_construct(                        -- Extra template-specific arguments here as name-value pairs, described above.
      'dimensions', ['p.STATUS'],          -- Any GROUP BY columns to show in the results.
      'measure_column', ['p.DAYS_ACTIVE'], -- Any aggregation columns to show in the results.
      'measure_type', ['AVG'],             -- Corresponding aggregation functions to apply to measure_column columns.
      'where_clause', 'p.HASHED_EMAIL=c.HASHED_EMAIL'   -- Specify one or more pairs of join columns here.
                                                        -- $$ is used to pass a string literal
    )
);

# Clean up

If you created the clean room, here is how to remove it from your account, so someone else can run this notebook after you.

In [ ]:
-- Consumer clean up
CALL samooha_by_snowflake_local_db.consumer.uninstall_cleanroom($cleanroom_name);

In [ ]:
-- Provider clean up
CALL samooha_by_snowflake_local_db.provider.drop_cleanroom($cleanroom_name);

# Troubleshooting

If you get a 'not approved:unauthorized columns used' error as a result of run analysis, you might want to view the join policy and
column policy set by the provider:

In [ ]:
CALL samooha_by_snowflake_local_db.consumer.view_provider_join_policy($cleanroom_name);
CALL samooha_by_snowflake_local_db.consumer.view_provider_column_policy($cleanroom_name);

It's also possible that you might have exhausted your privacy budget, which prevents you from running more queries. Check your remaining
privacy budget using the following stored procedure:

In [ ]:
CALL samooha_by_snowflake_local_db.consumer.view_remaining_privacy_budget($cleanroom_name);

To check if differential privacy has been enabled for the clean room, execute the following stored procedure:

In [ ]:
CALL samooha_by_snowflake_local_db.consumer.is_dp_enabled($cleanroom_name);